In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.figure_factory as ff
import pandas as pd
from sklearn.impute import SimpleImputer

In [40]:
file_path = ['../Project1_data/R98.xlsx', '../Project1_data/R99.xlsx',
             '../Project1_data/R1401.xlsx', '../Project1_data/R1400.xlsx',
             '../Project1_data/U98.xlsx', '../Project1_data/U99.xlsx',
             '../Project1_data/U1401.xlsx', '../Project1_data/U1400.xlsx']

# Map for accessinng dataFrames of each year easily
file_to_dfs_map = {}

for path in file_path: 
    
    file_identifier = path.split('/')[-1].split('.')[0]
    dataframes_list = []

    excel_file = pd.ExcelFile(path)
    sheetNames = excel_file.sheet_names
    

    for sheet in sheetNames:
        df_name = f'df_{sheet}'  # Create a dynamic DataFrame name
        globals()[df_name] = pd.read_excel(path, sheet_name=sheet)
        dataframes_list.append(df_name)
        print(f'{df_name} DataFrame created with shape: {globals()[df_name].shape}')
    
    file_to_dfs_map[file_identifier] = dataframes_list

df_R98Data DataFrame created with shape: (18430, 17)
df_R98P1 DataFrame created with shape: (64296, 10)
df_R98P2 DataFrame created with shape: (18430, 45)
df_R98P3S01 DataFrame created with shape: (516798, 7)
df_R98P3S02 DataFrame created with shape: (4175, 7)
df_R98P3S03 DataFrame created with shape: (22378, 4)
df_R98P3S04 DataFrame created with shape: (68767, 5)
df_R98P3S05 DataFrame created with shape: (87170, 4)
df_R98P3S06 DataFrame created with shape: (30600, 4)
df_R98P3S07 DataFrame created with shape: (35450, 4)
df_R98P3S08 DataFrame created with shape: (28627, 4)
df_R98P3S09 DataFrame created with shape: (10839, 4)
df_R98P3S10 DataFrame created with shape: (0, 4)
df_R98P3S11 DataFrame created with shape: (11269, 4)
df_R98P3S12 DataFrame created with shape: (67753, 4)
df_R98P3S13 DataFrame created with shape: (197127, 3)
df_R98P3S14 DataFrame created with shape: (4387, 4)
df_R98P4S01 DataFrame created with shape: (10820, 19)
df_R98P4S02 DataFrame created with shape: (14339, 19)

In [7]:
def fill_p1_age_under_6(df_name):
    temp = df_name[df_name['age'] <= 6].copy()

    temp['literacy'] = temp['literacy'].fillna('illiterate')
    temp['studying'] = temp['studying'].fillna('No')
    temp['degree'] = temp['degree'].fillna('illisterate')
    temp['occupationalst'] = temp['occupationalst'].fillna('child')
    temp['maritalst'] = temp['maritalst'].fillna('single')

    df_name.update(temp)

# After_p2_age_under_6 some persons which all of them was illiterate, have nan in bot studying and degree columns
# and this method is for filling them
def fill_study_degree(df_name):
    temp = df_name[pd.isna(df_name['studying'])]

    temp['studying'] = temp['studying'].fillna('No')
    temp['degree'] = temp['degree'].fillna('illiterate')

    df_name.update(temp)

# All the remaining nan values is for childs with age lower than 9, So I fill the nan vals wiht:
def fill_occ_mar(df_name):
    temp = df_name[pd.isna(df_name['occupationalst']) & df_name['age'] < 12]

    temp['occupationalst'] = temp['occupationalst'].fillna('child')
    temp['maritalst'] = temp['maritalst'].fillna('No')

    df_name.update(temp)

In [8]:
def fill_missing_with_mode(df):
    # Copy the original dataframe to avoid modifying it directly
    temp_df = df.copy()

    # Select columns 5 to 45 (adjusting for 0-based indexing, so columns 5:45)
    cols_to_impute = temp_df.iloc[:, 5:45].select_dtypes(include=['object']).columns

    # Initialize the SimpleImputer with the mode strategy (most frequent value)
    imputer = SimpleImputer(strategy='most_frequent')

    # Apply the imputer to the selected columns and fill missing values
    temp_df[cols_to_impute] = imputer.fit_transform(temp_df[cols_to_impute])

    return temp_df

In [37]:
def p3_s01_cleaner(df_name):
    df_name.drop(index = df_name[(pd.isna(df_name['value']))].index, inplace= True)
    df_name['gram'] = df_name['gram'].replace('\n', 0)
    df_name['gram'] = df_name['gram'].replace('   ', 0)
    df_name['gram'] = pd.to_numeric(df_name['gram'].fillna(0))
    df_name['kilogram'] = df_name['kilogram'].fillna(0)
    df_name['weight'] = df_name['gram'] + df_name['kilogram']
    df_name.drop(columns= ['gram', 'kilogram'], inplace= True)

In [10]:
def fill_p3_02(df_name):
    #drop gram column
    df_name.drop(columns= ['gram'], inplace= True)

In [39]:
def fill_p3_13(df_name):
    df_name['value'].replace('          ',  0, inplace= True)
    df_name['value'].replace('            ',  0, inplace= True)
    df_name['value'] = pd.to_numeric(df_name['value'])
    fill_value = df_name.groupby(by= 'code')['value'].transform('median')
    df_name['value'] = df_name['value'].fillna(fill_value)

In [12]:
def clean_p4_01(df_name):
    df_name.drop(columns= ['DYCOL00'], inplace= True)
    df_name['hours_w'] = df_name['hours_w'].fillna(0)
    df_name['days_w'] = df_name['days_w'].fillna(0)
    df_name[['wage_w_m', 'wage_w_y', 'perk_w_m', 'perk_w_y']] = df_name.groupby(['Address', 'member'])[['wage_w_m', 'wage_w_y', 'perk_w_m', 'perk_w_y']].transform('median')

In [13]:
def clean_p4_03(df_name):
    df_name['income_pension'] = df_name['income_pension'].replace('\n', 0)
    df_name['income_pension'] = pd.to_numeric(df_name['income_pension'])
    df_name['income_pension'] = df_name['income_pension'].fillna(0)
    df_name['income_rent'] = df_name['income_rent'].replace('\n', 0)
    df_name['income_rent'] = pd.to_numeric(df_name['income_rent'])
    df_name['income_rent'] = df_name['income_rent'].fillna(0)
    
    #fill cols = ['income_interest', 'income_aid', 'income_resale', 'income_transfer'] with 0

    cols = ['income_interest', 'income_aid', 'income_resale', 'income_transfer']

    for col in cols:
        df_name[col] = df_name[col].fillna(0)

In [41]:
files = file_to_dfs_map.keys()

for file in files:
    print(f'{file_to_dfs_map[file][1]} is cleaning')
    print('-' * 100)

    fill_p1_age_under_6(globals()[file_to_dfs_map[file][1]])
    fill_study_degree(globals()[file_to_dfs_map[file][1]])
    fill_occ_mar(globals()[file_to_dfs_map[file][1]])
    print(f'p1 is complete')

    print(f'{file_to_dfs_map[file][2]} is cleaning')
    globals()[file_to_dfs_map[file][2]] = fill_missing_with_mode(globals()[file_to_dfs_map[file][2]])
    print(f'p2 is complete')

    print(f'{file_to_dfs_map[file][3]} is cleaning')
    p3_s01_cleaner(globals()[file_to_dfs_map[file][3]])

    print(f'{file_to_dfs_map[file][4]} is cleaning')
    fill_p3_02(globals()[file_to_dfs_map[file][4]])

    print(f'{file_to_dfs_map[file][15]} is cleaning')
    fill_p3_13(globals()[file_to_dfs_map[file][15]])
    print(f'p3 is complete')

    print(f'{file_to_dfs_map[file][17]} is cleaning')
    clean_p4_01(globals()[file_to_dfs_map[file][17]])
    
    print(f'{file_to_dfs_map[file][19]}')
    clean_p4_03(globals()[file_to_dfs_map[file][19]])
    print(f'p4 is complete')

df_R98P1 is cleaning
----------------------------------------------------------------------------------------------------
p1 is complete
df_R98P2 is cleaning
p2 is complete
df_R98P3S01 is cleaning
df_R98P3S02 is cleaning
df_R98P3S13 is cleaning


C:\Users\Poumi008\AppData\Local\Temp\ipykernel_25952\2740681815.py:2: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  df_name['value'].replace('          ',  0, inplace= True)
C:\Users\Poumi008\AppData\Local\Temp\ipykernel_25952\2740681815.py:3: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a

p3 is complete
df_R98P4S01 is cleaning
df_R98P4S03
p4 is complete
df_R99P1 is cleaning
----------------------------------------------------------------------------------------------------
p1 is complete
df_R99P2 is cleaning
p2 is complete
df_R99P3S01 is cleaning
df_R99P3S02 is cleaning
df_R99P3S13 is cleaning
p3 is complete
df_R99P4S01 is cleaning
df_R99P4S03


C:\Users\Poumi008\AppData\Local\Temp\ipykernel_25952\2740681815.py:2: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  df_name['value'].replace('          ',  0, inplace= True)
C:\Users\Poumi008\AppData\Local\Temp\ipykernel_25952\2740681815.py:3: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a

p4 is complete
df_R1401P1 is cleaning
----------------------------------------------------------------------------------------------------
p1 is complete
df_R1401P2 is cleaning
p2 is complete
df_R1401P3S01 is cleaning
df_R1401P3S02 is cleaning
df_R1401P3S13 is cleaning


...

C:\Users\Poumi008\AppData\Local\Temp\ipykernel_25952\2740681815.py:2: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  df_name['value'].replace('          ',  0, inplace= True)
C:\Users\Poumi008\AppData\Local\Temp\ipykernel_25952\2740681815.py:3: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a

p3 is complete
df_U99P4S01 is cleaning
df_U99P4S03
p4 is complete
df_U1401P1 is cleaning
----------------------------------------------------------------------------------------------------
p1 is complete
df_U1401P2 is cleaning
p2 is complete
df_U1401P3S01 is cleaning
df_U1401P3S02 is cleaning
df_U1401P3S13 is cleaning


C:\Users\Poumi008\AppData\Local\Temp\ipykernel_25952\2740681815.py:2: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  df_name['value'].replace('          ',  0, inplace= True)
C:\Users\Poumi008\AppData\Local\Temp\ipykernel_25952\2740681815.py:3: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a

p3 is complete
df_U1401P4S01 is cleaning
df_U1401P4S03
p4 is complete
df_U1400P1 is cleaning
----------------------------------------------------------------------------------------------------
p1 is complete
df_U1400P2 is cleaning
p2 is complete
df_U1400P3S01 is cleaning
df_U1400P3S02 is cleaning
df_U1400P3S13 is cleaning
p3 is complete
df_U1400P4S01 is cleaning
df_U1400P4S03
p4 is complete


C:\Users\Poumi008\AppData\Local\Temp\ipykernel_25952\2740681815.py:2: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  df_name['value'].replace('          ',  0, inplace= True)
C:\Users\Poumi008\AppData\Local\Temp\ipykernel_25952\2740681815.py:3: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a

In [52]:
file_name_list = file_to_dfs_map.keys()
for file in file_name_list:
    dfs = []
    for df_name in file_to_dfs_map[file]:
        dfs.append(globals()[df_name])
    
    with pd.ExcelWriter(f'{file}.xlsx') as writer:
        for df, sheet in zip(dfs, file_to_dfs_map[file]):
            print(sheet)
            df.to_excel(writer, sheet_name=sheet, index=False)

df_R98Data
df_R98P1
df_R98P2
df_R98P3S01
df_R98P3S02
df_R98P3S03
df_R98P3S04
df_R98P3S05
df_R98P3S06
df_R98P3S07
df_R98P3S08
df_R98P3S09
df_R98P3S10
df_R98P3S11
df_R98P3S12
df_R98P3S13
df_R98P3S14
df_R98P4S01
df_R98P4S02
df_R98P4S03
df_R98P4S04
df_R99Data
df_R99P1
df_R99P2
df_R99P3S01
df_R99P3S02
df_R99P3S03
df_R99P3S04
df_R99P3S05
df_R99P3S06
df_R99P3S07
df_R99P3S08
df_R99P3S09
df_R99P3S10
df_R99P3S11
df_R99P3S12
df_R99P3S13
df_R99P3S14
df_R99P4S01
df_R99P4S02
df_R99P4S03
df_R99P4S04
df_R1401Data
df_R1401P1
df_R1401P2
df_R1401P3S01
df_R1401P3S02
df_R1401P3S03
df_R1401P3S04
df_R1401P3S05
df_R1401P3S06
df_R1401P3S07
df_R1401P3S08
df_R1401P3S09
df_R1401P3S10
df_R1401P3S11
df_R1401P3S12
df_R1401P3S13
df_R1401P3S14
df_R1401P4S01
df_R1401P4S02
df_R1401P4S03
df_R1401P4S04
df_R1400Data
df_R1400P1
df_R1400P2
df_R1400P3S01
df_R1400P3S02
df_R1400P3S03
df_R1400P3S04
df_R1400P3S05
df_R1400P3S06
df_R1400P3S07
df_R1400P3S08
df_R1400P3S09
df_R1400P3S10
df_R1400P3S11
df_R1400P3S12
df_R1400P3S13
df_R14

In [47]:
file_to_dfs_map['R98']

['df_R98Data',
 'df_R98P1',
 'df_R98P2',
 'df_R98P3S01',
 'df_R98P3S02',
 'df_R98P3S03',
 'df_R98P3S04',
 'df_R98P3S05',
 'df_R98P3S06',
 'df_R98P3S07',
 'df_R98P3S08',
 'df_R98P3S09',
 'df_R98P3S10',
 'df_R98P3S11',
 'df_R98P3S12',
 'df_R98P3S13',
 'df_R98P3S14',
 'df_R98P4S01',
 'df_R98P4S02',
 'df_R98P4S03',
 'df_R98P4S04']

In [48]:
dfs

[]

In [36]:
file_to_dfs_map.keys()

dict_keys(['R98', 'R99', 'R1401', 'R1400', 'U98', 'U99', 'U1401', 'U1400'])

In [7]:
file_to_dfs_map['R98']

['df_R98Data',
 'df_R98P1',
 'df_R98P2',
 'df_R98P3S01',
 'df_R98P3S02',
 'df_R98P3S03',
 'df_R98P3S04',
 'df_R98P3S05',
 'df_R98P3S06',
 'df_R98P3S07',
 'df_R98P3S08',
 'df_R98P3S09',
 'df_R98P3S10',
 'df_R98P3S11',
 'df_R98P3S12',
 'df_R98P3S13',
 'df_R98P3S14',
 'df_R98P4S01',
 'df_R98P4S02',
 'df_R98P4S03',
 'df_R98P4S04']

In [32]:
temp1 = globals()[file_to_dfs_map['R1401'][3]].copy()

In [33]:
temp1

Address   code  purchased    price    value  weight
0       20205408326  11615          1   550000  1100000     2.0
1       20205408326  11616          1   450000  1350000     3.0
2       20205408326  11641          1   120000   600000     5.0
3       20205408326  11642          1    85000   765000     9.0
4       20205408326  11652          1   700000   700000     1.0
...             ...    ...        ...      ...      ...     ...
489671  20204407941  11811          1   320000   320000     1.0
489672  20204407941  11913          1  2000000    60000    30.0
489673  20204407941  11921          1   475000   380000   800.0
489674  20204407941  12112          1  2400000  1200000   500.0
489675  20204407941  12211          1        0   300000     0.0

[489676 rows x 6 columns]

In [42]:
file_to_dfs_map['R98'][0]

'df_R98Data'

In [54]:
temp1[pd.isna(temp1['TakmilDescA']) & pd.isna(temp1['TakmilDescB']) & pd.isna(temp1['TakmilDescC']) & pd.isna(temp1['Jaygozin']) & pd.isna(temp1['JaygozinDescA']) & pd.isna(temp1['JaygozinDescB']) & pd.isna(temp1['JaygozinDescC']) & temp1['Takmil'] == 1]

Address  MahMorajeh  Fasl      weight  khanevartype  Takmil  \
0      20001383908           5     2  171.199524             1       1   
3      20001383916           5     2  171.199524             1       1   
5      20001383923           5     2  171.199524             1       1   
7      20001384011           8     3  171.199524             1       1   
8      20001384014           8     3  171.199524             1       1   
...            ...         ...   ...         ...           ...     ...   
18419  23006709617           5     2   84.791023             1       1   
18422  23006709709           9     3   84.791023             1       1   
18424  23006709716           9     3   84.791023             1       1   
18427  23006709723           9     3   84.791023             1       1   
18428  23006709807           1     4  254.373068             1       1   

       TakmilDescA  TakmilDescB TakmilDescC  Jaygozin  JaygozinDescA  \
0              NaN          NaN         NaN       NaN            NaN   
3              NaN          NaN         NaN       NaN            NaN   
5              NaN          NaN         NaN       NaN            NaN   
7              NaN          NaN         NaN       NaN            NaN   
8              NaN          NaN         NaN       NaN            NaN   
...            ...          ...         ...       ...            ...   
18419          NaN          NaN         NaN       NaN            NaN   
18422          NaN          NaN         NaN       NaN            NaN   
18424          NaN          NaN         NaN       NaN            NaN   
18427          NaN          NaN         NaN       NaN            NaN   
18428          NaN          NaN         NaN       NaN            NaN   

       JaygozinDescB  JaygozinDescC  BlkAbdJaygozin  RadifJaygozin province  \
0                NaN            NaN             NaN            NaN  Markazi   
3                NaN            NaN             NaN            NaN  Markazi   
5                NaN            NaN             NaN            NaN  Markazi   
7                NaN            NaN             NaN            NaN  Markazi   
8                NaN            NaN             NaN            NaN  Markazi   
...              ...            ...             ...            ...      ...   
18419            NaN            NaN             NaN            NaN   Alborz   
18422            NaN            NaN             NaN            NaN   Alborz   
18424            NaN            NaN             NaN            NaN   Alborz   
18427            NaN            NaN             NaN            NaN   Alborz   
18428            NaN            NaN             NaN            NaN   Alborz   

       town  
0         1  
3         1  
5         1  
7         1  
8         1  
...     ...  
18419     6  
18422     6  
18424     6  
18427     6  
18428     6  

[14517 rows x 17 columns]

In [60]:
temp1[temp1['Takmil'] == 2].info()

<class 'pandas.core.frame.DataFrame'>
Index: 3913 entries, 1 to 18429
Data columns (total 17 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   Address         3913 non-null   int64  
 1   MahMorajeh      3913 non-null   int64  
 2   Fasl            3913 non-null   int64  
 3   weight          3913 non-null   float64
 4   khanevartype    3913 non-null   int64  
 5   Takmil          3913 non-null   int64  
 6   TakmilDescA     0 non-null      float64
 7   TakmilDescB     3480 non-null   float64
 8   TakmilDescC     25 non-null     object 
 9   Jaygozin        3480 non-null   float64
 10  JaygozinDescA   0 non-null      float64
 11  JaygozinDescB   0 non-null      float64
 12  JaygozinDescC   0 non-null      float64
 13  BlkAbdJaygozin  3480 non-null   float64
 14  RadifJaygozin   3480 non-null   float64
 15  province        3913 non-null   object 
 16  town            3913 non-null   int64  
dtypes: float64(9), int64(6), object(2)
me

In [55]:
temp1[pd.isna(temp1['TakmilDescA']) & pd.isna(temp1['TakmilDescB']) & pd.isna(temp1['TakmilDescC']) & pd.isna(temp1['Jaygozin']) & pd.isna(temp1['JaygozinDescA']) & pd.isna(temp1['JaygozinDescB']) & pd.isna(temp1['JaygozinDescC'])]

Address    MahMorajeh          Fasl        weight  khanevartype  \
count  1.495000e+04  14950.000000  14950.000000  14950.000000  14950.000000   
mean   2.147673e+10      6.486288      2.471839    338.322379      1.000334   
std    8.945645e+08      3.424410      1.113039    269.238495      0.018285   
min    2.000138e+10      1.000000      1.000000     41.022802      1.000000   
25%    2.071047e+10      3.000000      1.000000    144.557998      1.000000   
50%    2.140755e+10      6.000000      2.000000    283.909353      1.000000   
75%    2.221063e+10      9.000000      3.000000    454.469265      1.000000   
max    2.300671e+10     12.000000      4.000000   5254.802639      2.000000   

             Takmil  TakmilDescA  TakmilDescB  Jaygozin  JaygozinDescA  \
count  14950.000000          0.0          0.0       0.0            0.0   
mean       1.028963          NaN          NaN       NaN            NaN   
std        0.167709          NaN          NaN       NaN            NaN   
min        1.000000          NaN          NaN       NaN            NaN   
25%        1.000000          NaN          NaN       NaN            NaN   
50%        1.000000          NaN          NaN       NaN            NaN   
75%        1.000000          NaN          NaN       NaN            NaN   
max        2.000000          NaN          NaN       NaN            NaN   

       JaygozinDescB  JaygozinDescC  BlkAbdJaygozin  RadifJaygozin  \
count            0.0            0.0             0.0            0.0   
mean             NaN            NaN             NaN            NaN   
std              NaN            NaN             NaN            NaN   
min              NaN            NaN             NaN            NaN   
25%              NaN            NaN             NaN            NaN   
50%              NaN            NaN             NaN            NaN   
75%              NaN            NaN             NaN            NaN   
max              NaN            NaN             NaN            NaN   

               town  
count  14950.000000  
mean       7.717258  
std        6.422468  
min        1.000000  
25%        3.000000  
50%        6.000000  
75%       10.000000  
max       39.000000

In [43]:
temp1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18430 entries, 0 to 18429
Data columns (total 17 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   Address         18430 non-null  int64  
 1   MahMorajeh      18430 non-null  int64  
 2   Fasl            18430 non-null  int64  
 3   weight          18430 non-null  float64
 4   khanevartype    18430 non-null  int64  
 5   Takmil          18430 non-null  int64  
 6   TakmilDescA     0 non-null      float64
 7   TakmilDescB     3480 non-null   float64
 8   TakmilDescC     25 non-null     object 
 9   Jaygozin        3480 non-null   float64
 10  JaygozinDescA   0 non-null      float64
 11  JaygozinDescB   0 non-null      float64
 12  JaygozinDescC   0 non-null      float64
 13  BlkAbdJaygozin  3480 non-null   float64
 14  RadifJaygozin   3480 non-null   float64
 15  province        18430 non-null  object 
 16  town            18430 non-null  int64  
dtypes: float64(9), int64(6), object

In [ ]:
temp1.groupby(by= ['code'])['value'].transform('median')

In [63]:
temp1[temp1['purchased'] == '8']

count    1.454000e+03
mean     2.003459e+06
std      1.686867e+06
min      1.000000e+05
25%      1.000000e+06
50%      1.500000e+06
75%      2.500000e+06
max      2.500000e+07
Name: value, dtype: float64

In [ ]:
def fill_p3_04(df_name):
    index_mmortgage = df_name[df_name['purchased'] == '8'].index
    df_name.loc[index_mmortgage, 'mortgage'] = 0

In [76]:
temp1[(temp1['purchased'] == '1') & ~pd.isna(temp1['mortgage'])]

Address   code      mortgage purchased     value
208    20007391408  42212  1.000000e+07         1    300000
285    20005388614  42212  1.000000e+07         1    300000
1379   20215411908  42212  3.000000e+08         1   9000000
1501   20219413520  42212  1.500000e+07         1    450000
1691   20210410717  42212  1.000000e+08         1   3000000
...            ...    ...           ...       ...       ...
68561  23002704217  42212  1.000000e+08         1   3000000
68565  23002704214  42212  7.000000e+07         1   2100000
68637  23006709014  42212  5.000000e+08         1  15000000
68720  23002704623  42212  5.000000e+08         1  15000000
68760  23006709423  42212  1.000000e+09         1  30000000

[614 rows x 5 columns]

In [74]:
temp1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 68767 entries, 0 to 68766
Data columns (total 5 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   Address    68767 non-null  int64  
 1   code       68767 non-null  int64  
 2   mortgage   2068 non-null   float64
 3   purchased  52784 non-null  object 
 4   value      68767 non-null  int64  
dtypes: float64(1), int64(3), object(1)
memory usage: 2.6+ MB


In [66]:
temp1['purchased'].unique()

array([nan, '1', '8', '5', '2', '3', ' ', '4', '7', '6'], dtype=object)

In [56]:
temp1.head(10)

Address   code  mortgage purchased    value
0  20011395420  42111       NaN       NaN  1000000
1  20011395420  44418       NaN         1    20000
2  20011395420  45111       NaN         1   350000
3  20011395420  45211       NaN         1   200000
4  20001385412  42111       NaN       NaN  1500000
5  20001385412  44111       NaN         1   300000
6  20001385412  45111       NaN         1   300000
7  20001385412  45211       NaN         1   700000
8  20001385423  42111       NaN       NaN  2000000
9  20001385423  44111       NaN         1   100000

In [55]:
temp1.groupby

Address
23006709014    8
23006708415    8
23006709210    8
23006709423    7
23006709116    7
              ..
21910599815    1
21910599808    1
21906596620    1
22210629423    1
22210629415    1
Name: count, Length: 18430, dtype: int64

In [52]:
pd.set_option('display.max_rows', 100)

In [54]:
temp1.describe()

Address          code      mortgage         value
count  6.876700e+04  68767.000000  6.140000e+02  6.876700e+04
mean   2.145774e+10  44076.659880  1.007756e+08  9.694461e+05
std    9.298514e+08   1306.872948  1.194424e+08  1.722758e+06
min    2.000138e+10  41111.000000  1.200000e+06  4.000000e+03
25%    2.062446e+10  42212.000000  2.000000e+07  1.600000e+05
50%    2.140455e+10  44418.000000  5.000000e+07  3.300000e+05
75%    2.230363e+10  45211.000000  1.500000e+08  1.000000e+06
max    2.300671e+10  45414.000000  1.000000e+09  6.500000e+07

In [53]:
temp1['mortgage'].describe()

count    6.140000e+02
mean     1.007756e+08
std      1.194424e+08
min      1.200000e+06
25%      2.000000e+07
50%      5.000000e+07
75%      1.500000e+08
max      1.000000e+09
Name: mortgage, dtype: float64

In [51]:
temp1[pd.isna(temp1['purchased'])]

Address   code  mortgage purchased     value
0      20011395420  42111       NaN       NaN   1000000
4      20001385412  42111       NaN       NaN   1500000
8      20001385423  42111       NaN       NaN   2000000
13     20001385420  42111       NaN       NaN   1200000
21     20012396607  42111       NaN       NaN    300000
26     20010394223  42111       NaN       NaN   1000000
35     20004387823  42111       NaN       NaN   1200000
44     20011395416  42111       NaN       NaN    800000
48     20013397823  42111       NaN       NaN   2000000
52     20013397814  42111       NaN       NaN    700000
57     20013397820  42111       NaN       NaN    700000
67     20011395411  42111       NaN       NaN    800000
70     20005389011  42111       NaN       NaN   1500000
74     20005389018  42111       NaN       NaN    300000
79     20005389020  42111       NaN       NaN   1500000
83     20005389023  42111       NaN       NaN    200000
84     20012396614  42111       NaN       NaN   1000000
89     20005389014  42111       NaN       NaN   1500000
93     20007392611  42111       NaN       NaN   1300000
97     20007392615  42111       NaN       NaN    900000
101    20007392623  42111       NaN       NaN   1400000
105    20003386613  42111       NaN       NaN    800000
111    20004387809  42111       NaN       NaN   1700000
116    20004387817  42111       NaN       NaN   1500000
121    20004387820  42111       NaN       NaN   1200000
125    20004387811  42111       NaN       NaN   2500000
134    20003386614  42111       NaN       NaN   2000000
138    20010394211  42111       NaN       NaN    200000
139    20010394217  42111       NaN       NaN   2000000
143    20010394208  42111       NaN       NaN   1500000
147    20004387813  42111       NaN       NaN   2000000
152    20003386610  42111       NaN       NaN    200000
155    20010394214  42111       NaN       NaN    200000
159    20012396620  42111       NaN       NaN   1000000
164    20012396609  42111       NaN       NaN   1500000
169    20013397807  42111       NaN       NaN    800000
178    20013397817  42111       NaN       NaN   1000000
182    20012396617  42111       NaN       NaN   1000000
187    20006390211  42111       NaN       NaN   1000000
195    20007392620  42111       NaN       NaN   1400000
199    20007392616  42111       NaN       NaN   1000000
216    20005389008  42111       NaN       NaN   1000000
224    20001385415  42111       NaN       NaN   1500000
228    20001385408  42111       NaN       NaN   2000000
232    20007391423  42111       NaN       NaN   1100000
236    20001384214  42111       NaN       NaN   2000000
240    20007391820  42111       NaN       NaN    700000
244    20001384223  42111       NaN       NaN   3500000
248    20001384207  42111       NaN       NaN   2500000
252    20001384208  42111       NaN       NaN   3000000
256    20001384215  42111       NaN       NaN   3000000
260    20001384220  42111       NaN       NaN   2700000
264    20004387408  42111       NaN       NaN   2000000
269    20004387417  42111       NaN       NaN    700000
274    20012395814  42111       NaN       NaN   3500000
279    20005388620  42111       NaN       NaN   2000000
291    20007391811  42111       NaN       NaN    650000
299    20007391814  42111       NaN       NaN    300000
303    20007391817  42111       NaN       NaN    500000
307    20007391808  42111       NaN       NaN    600000
311    20003387023  42111       NaN       NaN   1000000
315    20003387008  42111       NaN       NaN    300000
329    20003387007  42111       NaN       NaN    500000
333    20012395820  42111       NaN       NaN   2000000
337    20003387014  42111       NaN       NaN   1000000
341    20003387017  42111       NaN       NaN    950000
345    20002385814  42111       NaN       NaN   1000000
349    20002385823  42111       NaN       NaN   1000000
353    20002385808  42111       NaN       NaN   2300000
358    20002385811  42111       NaN       NaN   2000000
365    20013397020  42111       NaN

In [173]:
temp2 = temp1.copy()
map_undo = {}

for col in temp2.iloc[:, 5:45].select_dtypes(include=['object']).columns:

    values_of_material = temp2[col].value_counts().sort_index(ascending= False).index

    mapping = {val: idx for idx, val in enumerate(values_of_material)}
    mapping_undo = {idx: val for idx, val in enumerate(values_of_material)}

    map_undo[col] = mapping_undo

    temp2[col] = temp2[col].map(mapping)

In [ ]:
def redo_mapping(df_name):
    for col in df_name.iloc[:, 5:45].select_dtypes(include=['object']).columns:

        df_name[col] = df_name.map(map_undo[col])

In [165]:
temp2.shape

(18430, 45)

In [166]:
temp2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18430 entries, 0 to 18429
Data columns (total 45 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   Address              18430 non-null  int64  
 1   tenure               18430 non-null  object 
 2   room                 18430 non-null  int64  
 3   space                18430 non-null  int64  
 4   construction         18430 non-null  int64  
 5   material             14816 non-null  float64
 6   vehicle              18430 non-null  bool   
 7   motorcycle           18430 non-null  bool   
 8   bicycle              18430 non-null  bool   
 9   radio                18430 non-null  bool   
 10  radiotape            18430 non-null  bool   
 11  TVbw                 18430 non-null  bool   
 12  TV                   18430 non-null  bool   
 13  VHS_VCD_DVD          18430 non-null  bool   
 14  computer             18430 non-null  bool   
 15  cellphone            18430 non-null 

In [171]:
import pandas as pd
from sklearn.impute import KNNImputer

# Assuming temp1 is your DataFrame

# Step 1: Identify the columns with missing values
columns_to_fill = temp2.columns[temp1.isnull().any()].tolist()

# Step 2: Define the range of columns (6 to 43) to use as features for KNN
columns_for_knn = temp2.columns[5:45]  # Columns from 6 to 43 (0-indexed)

# Step 3: Prepare the data for imputation
# Only select the columns that will be used for KNN (including the columns to fill)
data_for_knn = temp2[columns_for_knn]

# Step 4: Apply KNN imputer to the data
imputer = KNNImputer(n_neighbors=5)  # You can adjust the number of neighbors
data_imputed = imputer.fit_transform(data_for_knn)

# Step 5: Put the imputed data back into the original DataFrame
# Replace the original columns with the imputed data
temp2[columns_for_knn] = pd.DataFrame(data_imputed, columns=columns_for_knn, index=temp1.index)

# Step 6: Check if the missing values are filled
print(temp2[columns_to_fill].isnull().sum())  # This should return 0 for the four columns

material            0
cookingfuel         0
heatingfuel         0
waterheatingfuel    0
dtype: int64


In [172]:
temp2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18430 entries, 0 to 18429
Data columns (total 45 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   Address              18430 non-null  int64  
 1   tenure               18430 non-null  object 
 2   room                 18430 non-null  int64  
 3   space                18430 non-null  int64  
 4   construction         18430 non-null  int64  
 5   material             18430 non-null  float64
 6   vehicle              18430 non-null  float64
 7   motorcycle           18430 non-null  float64
 8   bicycle              18430 non-null  float64
 9   radio                18430 non-null  float64
 10  radiotape            18430 non-null  float64
 11  TVbw                 18430 non-null  float64
 12  TV                   18430 non-null  float64
 13  VHS_VCD_DVD          18430 non-null  float64
 14  computer             18430 non-null  float64
 15  cellphone            18430 non-null 

In [55]:
temp1[pd.isna(temp1['literacy'])]

32       NaN
39       NaN
47       NaN
62       NaN
71       NaN
        ... 
64241    NaN
64260    NaN
64271    NaN
64272    NaN
64287    NaN
Name: occupationalst, Length: 6239, dtype: object

In [71]:
temp1[(temp1['maritalst'] == 'Single')]['age'].min()

np.int64(9)

In [6]:
temp_df = globals()[file_to_dfs_map['R98'][1]].copy()

non_numeric_cols = temp_df.select_dtypes(include= ['object', 'category']).columns

for col in non_numeric_cols:
    # Step 3: Get the unique values using value_counts, sort them alphabetically
    unique_vals_sorted = temp_df[col].value_counts().index.sort_values()
    # print(unique_vals_sorted)
    # Step 4: Create a mapping from the unique values to numeric codes
    mapping = {val: idx for idx, val in enumerate(unique_vals_sorted)}
    
    # Step 5: Apply the mapping using .map()
    temp_df[col] = temp_df[col].map(mapping)

In [22]:
corr_mat = temp2.corr()

# Convert index to list for x and y
x = corr_mat.columns.tolist()
y = corr_mat.columns.tolist()

# Create annotated heatmap
fig = ff.create_annotated_heatmap(
    z=corr_mat.values,
    x=x,
    y=y,
    colorscale='Viridis'
)

# Update layout
fig.update_layout(
    title='Correlation Heatmap',
    xaxis_title='Features',
    yaxis_title='Features'
)

# Show figure
fig.show()

In [20]:
temp2 = temp_df.loc[:, ['literacy', 'degree']]

In [34]:
temp2.dropna(axis= 0, how= 'any').corr()

literacy  degree
literacy       NaN     NaN
degree         NaN     1.0

In [19]:
globals()[file_to_dfs_map['R98'][1]]['degree'].value_counts()

degree
3.0    21647
8.0    10061
2.0     6953
4.0     2439
0.0     2356
1.0      968
6.0      400
5.0      341
7.0       12
Name: count, dtype: int64

In [17]:
globals()[file_to_dfs_map['R98'][1]]

Address  member  relation  gender  age  literacy  studying  degree  \
0      20010394208       1         2       1   50       1.0       0.0     3.0   
1      20010394208       2         8       0   45       0.0       NaN     NaN   
2      20010394208       3         0       0   26       1.0       0.0     3.0   
3      20010394208       4         0       1   25       1.0       0.0     0.0   
4      20010394208       5         0       1   14       1.0       1.0     8.0   
...            ...     ...       ...     ...  ...       ...       ...     ...   
64291  23001701017       3         0       1   21       1.0       0.0     1.0   
64292  23001701020       1         2       1   57       1.0       0.0     8.0   
64293  23001701020       2         8       0   50       1.0       0.0     8.0   
64294  23001701020       3         0       1   26       1.0       1.0     0.0   
64295  23002703423       1         2       0   60       0.0       NaN     NaN   

       occupationalst  maritalst  
0                 4.0        1.0  
1                 0.0        1.0  
2                 0.0        1.0  
3                 4.0        2.0  
4                 3.0        2.0  
...               ...        ...  
64291             4.0        2.0  
64292             4.0        1.0  
64293             0.0        1.0  
64294             3.0        2.0  
64295             1.0        3.0  

[64296 rows x 10 columns]

In [21]:
for df in file_to_dfs_map['R98']:
    print(globals()[df].info())
    print('-' * 100)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18430 entries, 0 to 18429
Data columns (total 17 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   Address         18430 non-null  int64  
 1   MahMorajeh      18430 non-null  int64  
 2   Fasl            18430 non-null  int64  
 3   weight          18430 non-null  float64
 4   khanevartype    18430 non-null  int64  
 5   Takmil          18430 non-null  int64  
 6   TakmilDescA     0 non-null      float64
 7   TakmilDescB     3480 non-null   float64
 8   TakmilDescC     25 non-null     object 
 9   Jaygozin        3480 non-null   float64
 10  JaygozinDescA   0 non-null      float64
 11  JaygozinDescB   0 non-null      float64
 12  JaygozinDescC   0 non-null      float64
 13  BlkAbdJaygozin  3480 non-null   float64
 14  RadifJaygozin   3480 non-null   float64
 15  province        18430 non-null  object 
 16  town            18430 non-null  int64  
dtypes: float64(9), int64(6), object